In [ ]:
import re
import math
import datetime

from dataclasses import dataclass

from copy import copy

from openpyxl import load_workbook, Workbook
from openpyxl.styles import Color, PatternFill
from openpyxl.worksheet.table import Table

from spielbergerscripts.primitives.product import Product, Bundle
from spielbergerscripts.connector import IBMConnector

In [ ]:
# define some colors

yellow = Color(rgb='FFFF00')
red = Color(rgb='E6B8B7')
orange = Color(rgb='FCD5B4')
purple = Color(rgb='CCC0DA')
blue = Color(rgb='B8CCE4')

In [ ]:
# classes Abpackung, DispoBedarf, Leistungsdaten, Umbau, Vorlage

@dataclass
class Abpackung:
    artikelNummer:  int     # ArtNr
    abpackMenge:    int     # in KG
    bemerkung:      str
    planPos:        int     # Wochenplannummer
    bem_ek:         str     # Bemerkung Einkauf
    roh1:           str     # Rohstoff 1
    roh1_bes:       str     # Rohstoff 1 Bestand
    roh2:           str     # Rohstoff 2
    roh2_bes:       str     # Rohstoff 2 Bestand

    def anzBeutel(self, bundles):
        gg = bundles[self.artikelNummer]
        return int((self.abpackMenge * 1000) / gg.bagWeight)

    def anzGebinde(self, bundles):
        gg = bundles[self.artikelNummer]
        return int(self.anzBeutel(bundles) / gg.nbrBags)

@dataclass
class MischBedarf:
    artikelNummer:  int     # ArtNr
    abpackMenge:    int     # in KG
    kw_reich:       float   # KW REICH
    bem_ek:         str     # Bemerkung Einkauf
    roh1:           str     # Rohstoff 1
    roh1_bes:       str     # Rohstoff 1 Bestand
    roh2:           str     # Rohstoff 2
    roh2_bes:       str     # Rohstoff 2 Bestand

@dataclass
class DispoBedarf:
    artikelNummer:  str     # ArtNr
    palettenziel:   int     # Menge / Soll Palette
    bestandL00:     int     # Cha BES00
    bestandL01:     int     # Cha BES00
    bestandL05:     int     # Cha BES05
    auftragsBestand:int     # Auf Bes
    bestellBestand: int     # Best Bes
    durchschnitt:   int     # Durchschnitt Bestellung pro Woche
    tuetenAnz:      int     # Anzahl Tüten Lager + HLB
    bem_ek:         str     # Bemerkung Einkauf
    roh1:           str     # Rohstoff 1
    roh1_bes:       str     # Rohstoff 1 Bestand
    roh2:           str     # Rohstoff 2
    roh2_bes:       str     # Rohstoff 2 Bestand

    def bestandFrei(self):
        return self.bestandL00 + self.bestandL05 + self.bestellBestand - self.auftragsBestand

    def reichweite(self, prodNeu = 0):
        return (self.bestandFrei() + prodNeu) / self.durchschnitt

    def reichweiteNeu(self, abpackDict, prodDict):
        abp = abpackDict.get(self.artikelNummer, None)
        if abp is None:
            return self.reichweite()

        return self.reichweite(abp.anzBeutel(prodDict))

@dataclass
class Leistungsdaten:
    artikelNummer:  str
    leistung:       dict    # Beutel / h pro Packerei (Pack1, Pack2, Pack3, Pack4)
    modi:           dict    # Produktionsmodus pro Packerei
    kurzBez:        str
    gebindeGr:      Bundle
    palettenMenge:  int
    muehle:         bool
    muehleMisch:    bool
    rezept:         bool
    gfProd:         bool
    duezi:          bool


@dataclass
class Umbauzeiten:
    pack:   str
    modi:   set
    umbau:  dict

@dataclass
class PackereiVorlage:
    packerei:   str
    beginn:     datetime.datetime
    vorlage:    str

In [ ]:
# read Vorlage, Leistugnsdaten, Umbauzeiten, Stammdaten, Leistungsdaten

def packVorlage(sheet):
    vorlage = dict()
    vorlage["Pack1"] = PackereiVorlage(
        packerei = sheet['A3'].value,
        beginn = sheet['B3'].value,
        vorlage = sheet['C3'].value,
    )
    vorlage["Pack2"] = PackereiVorlage (
        packerei = sheet['A4'].value,
        beginn = sheet['B4'].value,
        vorlage = sheet['C4'].value,
    )
    vorlage["Pack3"] = PackereiVorlage (
        packerei = sheet['A5'].value,
        beginn = sheet['B5'].value,
        vorlage = sheet['C5'].value,
    )
    vorlage["Pack4"] = PackereiVorlage (
        packerei = sheet['A6'].value,
        beginn = sheet['B6'].value,
        vorlage = sheet['C6'].value,
    )

    return vorlage

def getPackLeistung(artikelNummer):
    return LEISTUNGS_DICT.get(artikelNummer, LEISTUNGS_DICT["000000"])  

def getWechsel(modus, new_modus, pack):
    tWechsel = PROD_STAMM[pack].umbau.get((modus, new_modus), None)
    if tWechsel is None:
        return 20
    else:
        return tWechsel

def shortName(artikelNummer):
    return getPackLeistung(artikelNummer).kurzBez

def beutelProH(artikelNummer, packerei):
    return getPackLeistung(artikelNummer).leistung[packerei]

def readProdStamm(sheet, pack, offset):
    modi = []
    count = 0
    while True:
        c = sheet.cell(row=offset + 2 + count, column = 2).value
        if c is None:
            break
        modi.append(c)
        count += 1
    umbau = dict()
    for idxI, modI in enumerate(modi):
        for idxJ, modJ in enumerate(modi):
            umbau[modI, modJ] = int(sheet.cell(row=offset + 2 + idxJ, column=6+idxI).value)
    return Umbauzeiten(
        pack,
        modi,
        umbau
    )

def produktionStammdaten(sheet):
    return {
        "Pack1": readProdStamm(sheet, "Pack1", 1),
        "Pack2": readProdStamm(sheet, "Pack2", 11),
        "Pack3": readProdStamm(sheet, "Pack3", 30),
        "Pack4": readProdStamm(sheet, "Pack4", 36),
    }

def isSet(field):
    if field is None:
        return False
    if field != 1:
        return False
    return True

def packLeistung(sheet):
    leistungs_dict = {}
    for row in sheet.iter_rows(min_row=3, max_row=len(sheet['A']), max_col=18, values_only=True):
        if row[0] is None:
            continue
        l = Leistungsdaten(
            artikelNummer=row[0],
            leistung={
                "Pack1": int(row[1] if not (row[1] is None or row[1] == "#N/A") else 2000),
                "Pack2": int(row[3] if not (row[3] is None or row[3] == "#N/A") else 1000),
                "Pack3": int(row[5] if not (row[5] is None or row[5] == "#N/A") else 800),
                "Pack4": int(row[7] if not (row[7] is None or row[7] == "#N/A") else 60)
            },
            modi = {
                "Pack1": row[2],
                "Pack2": row[4],
                "Pack3": row[6],
                "Pack4": row[8]
            },
            kurzBez=row[9],
            gebindeGr=Bundle.fromString(row[10]),
            palettenMenge=int(row[11]),
            muehle = isSet(row[13]),
            muehleMisch = isSet(row[14]),
            rezept = isSet(row[15]),
            gfProd = isSet(row[16]),
            duezi = isSet(row[17])
        )
        leistungs_dict[l.artikelNummer] = l

    return leistungs_dict

In [ ]:
# read Dispo

def readDispo(sheet, prodStamm):
    DISPO_DICT = {}
    ABPACK_DICT = {}
    MISCH_DICT = {}
    GEB_GROESSE = {}
    HEADER = True
    for row in sheet.rows:

        if HEADER:                  # skip the header lines
            if row[0].value == "ARTNR":
                HEADER = False
            continue
        if row[0].value is None:
            break

        product = prodStamm.get(row[0].value, None)

        d = DispoBedarf(
            artikelNummer=row[0].value,
            palettenziel=row[4].value,
            bestandL00=row[5].value,
            bestandL01=row[6].value,
            bestandL05=row[7].value,
            auftragsBestand=row[8].value,
            bestellBestand=row[15].value,
            durchschnitt=row[17].value,
            tuetenAnz= 0 if row[24].value is None else int(float(row[24].value)*1000),
            roh1 = row[18].value,
            roh1_bes = row[20].value,
            roh2 = row[21].value,
            roh2_bes = row[22].value,
            bem_ek = row[23].value
        )

        g = Bundle.fromString(row[2].value)

        DISPO_DICT[d.artikelNummer] = d
        GEB_GROESSE[d.artikelNummer] = g

        if not (row[25].value is None):
            a = Abpackung(
                artikelNummer=d.artikelNummer,
                abpackMenge=int(row[25].value),
                bemerkung="",
                planPos= 999 if row[29].value is None else int(int(row[29].value)),
                roh1 = row[18].value,
                roh1_bes = row[20].value,
                roh2 = row[21].value,
                roh2_bes = row[22].value,
                bem_ek = row[23].value
            )

            ABPACK_DICT[d.artikelNummer]=a

        if not product is None and product.muehleMisch == 1:
            MISCH_DICT[d.artikelNummer] = MischBedarf(
                artikelNummer = d.artikelNummer,
                abpackMenge =   int(row[25].value) if not row[25].value is None else 0,
                kw_reich =      float(row[16].value),
                bem_ek =        row[23].value,
                roh1 = row[18].value,
                roh1_bes = row[20].value,
                roh2 = row[21].value,
                roh2_bes = row[22].value)

    return DISPO_DICT, ABPACK_DICT, GEB_GROESSE, MISCH_DICT

In [ ]:
# write Schedule
def writeMischDispo(vorlage, dP1, dP2, dP3, dP4, prodDict):
    name = f"MischDispo"
    sheet = vorlage.copy_worksheet(vorlage["MischDispo"])
    if name in vorlage.sheetnames:
        vorlage.remove(vorlage[name])
    vorlage.move_sheet(sheet, 1 - vorlage.index(sheet))
    sheet.title = name

    counter = 0
    for pack, mischDispo in [("Pack1", dP1), ("Pack2", dP2), ("Pack3", dP3), ("Pack4", dP4)]:
        for d in mischDispo.values():
            p = prodDict.get(d.artikelNummer, None)
            if p is None:
                print(f"ERROR: Product {p.artikelNummer} not found")
            counter += 1
            sheet.append([pack, d.artikelNummer, p.name, p.bundle, d.kw_reich, d.abpackMenge, d.bem_ek, d.roh1, d.roh1_bes, d.roh2, d.roh2_bes])

    tab = Table(displayName="MischDispo", ref=f"A1:K{counter}")
    sheet.add_table(tab)


def writeSchedule(vorlage, dispo, prodDict, pack):
    name = f"Schedule {pack}"

    _dispoDict, abpackDict, gebGroesse, _mischDict = dispo

    sheet = vorlage.copy_worksheet(vorlage["Schedule"])
    if name in vorlage.sheetnames:
        vorlage.remove(vorlage[name])
    vorlage.move_sheet(sheet, 1 - vorlage.index(sheet))
    sheet.title = name

    pas = list(abpackDict.values())
    pas.sort(key=lambda pa: pa.planPos)
    modus = None
    time = 0
    for pa in pas:
        leistung = getPackLeistung(pa.artikelNummer)
        if leistung.artikelNummer == "000000":
            print(f"Leistungsdaten für Produkt {pa.artikelNummer} nicht verfügbar!")
            
        #print(f"Trying to pack {pa.artikelNummer} with {beutelProH(pa.artikelNummer, pack)}")
        new_modus = leistung.modi[pack]
        if time != 0:
            if new_modus is None:
                print(f"Leistungsdaten für Produkt {pa.artikelNummer} auf Packerei {pack} nicht verfügbar!")
                time = writePAProdChange(sheet, time, 60, modus, f"Unbekannt - Leistungsdaten für {pa.artikelNummer} auf {pack} setzen und Leistungsdaten aktualisieren!")
            else:
                delta = getWechsel(modus, new_modus, pack)
                time = writePAProdChange(sheet, time, delta, modus, new_modus)

        if pa.abpackMenge is None or pa.abpackMenge == 0:
            print(f"Für Produkt {pa.artikelNummer} in Pack {pack} ist keine gültige Abpackmenge eingetragen")
            continue

        time = writePASchedule(sheet, pa, leistung, prodDict, gebGroesse, pack, time)
        modus = new_modus
    writeEnd(sheet)

def writeHeader(sheet):
    sheet.cell(row=1, column = 1).value = "ART.NR."
    sheet.cell(row=1, column = 2).value = "ART.BEZ."
    sheet.cell(row=1, column = 3).value = "GEBINDE"
    sheet.cell(row=1, column = 4).value = "MENGE"
    sheet.cell(row=1, column = 5).value = "GEBINDE"
    sheet.cell(row=1, column = 6).value = "BEUTEL"
    sheet.cell(row=1, column = 7).value = "PLANPOS"
    sheet.cell(row=1, column = 8).value = "BEUTEL/H"
    sheet.cell(row=1, column = 9).value = "DAUER"
    sheet.cell(row=1, column = 10).value = "ANMERKUNG"

def writeEnd(sheet):
    row = sheet.max_row + 1
    sheet.cell(row=row, column = 9).value = "30"
    sheet.cell(row=row, column = 10).value = "Schichtende"

def prodTime(nbrBags, performance, min_t = 30):
        return max(int(nbrBags * 60 / performance), min_t)

def writePASchedule(sheet, pa, l, prodDict, gebGroeDict, pack, start):
    row = sheet.max_row + 1
    geb = gebGroeDict[pa.artikelNummer]
    prod = prodDict[pa.artikelNummer]
    # t = math.ceil(60 * pa.anzBeutel(gebGroeDict) / beutelProH(pa.artikelNummer, pack))
    t = prodTime(pa.anzBeutel(gebGroeDict), beutelProH(pa.artikelNummer, pack))
    sheet.cell(row=row, column = 1).value = pa.artikelNummer
    sheet.cell(row=row, column = 2).value = shortName(pa.artikelNummer)
    sheet.cell(row=row, column = 3).value = geb.szBundle
    sheet.cell(row=row, column = 4).value = pa.abpackMenge
    sheet.cell(row=row, column = 5).value = pa.anzGebinde(gebGroeDict)
    sheet.cell(row=row, column = 6).value = pa.anzBeutel(gebGroeDict)
    sheet.cell(row=row, column = 7).value = pa.planPos
    sheet.cell(row=row, column = 8).value = beutelProH(pa.artikelNummer, pack)
    sheet.cell(row=row, column = 9).value = t
    sheet.cell(row=row, column = 10).value = pa.bemerkung
    sheet.cell(row=row, column = 11).value = pa.bem_ek
    sheet.cell(row=row, column = 12).value = pa.roh1
    sheet.cell(row=row, column = 13).value = pa.roh1_bes
    sheet.cell(row=row, column = 14).value = pa.roh2
    sheet.cell(row=row, column = 15).value = pa.roh2_bes

#    if l.muehleMisch:
#        for i in range(1,10):
#            sheet.cell(row=row, column=i).fill  = PatternFill(fgColor=purple, fill_type = 'solid')
    if l.muehle:
        for i in range(1,10):
            sheet.cell(row=row, column=i).fill  = PatternFill(fgColor=blue, fill_type = 'solid')

    return start + t

def writePAProdChange(sheet, start, delta, modFrom, modTo):
    row = sheet.max_row + 1
    sheet.cell(row=row, column = 9).value = delta
    if modFrom != modTo:
        sheet.cell(row=row, column = 10).value = f"Umbau auf {modTo}"

    return start + delta

In [ ]:
# Workday
@dataclass
class Workday:
    begin:      int
    end:        int
    breaks:     list

    def to_holliday():
        return Workday(0, 0, [])

    def to_1_schicht_WU(begin, end=None):
        return Workday(begin, begin + 9 if end is None else end, [3 * 60, 6 * 60])

    def to_1_schicht(begin, end=None):
        return Workday(begin, begin + 9.5 if end is None else end, [2.5 * 60, 6 * 60])
        
    def to_2_schicht(begin, end=None):
        return Workday(begin, begin + 18 if end is None else end, [3 * 60, 6.5 * 60, 12 * 60, 15.5 * 60])

    def to_2_schicht_one_only(begin, end=None):
        return Workday(begin, begin + 9 if end is None else end, [3 * 60, 6.5 * 60])

    def to_3_schicht(begin, end=None):
        return Workday(begin, begin + 24 if end is None else end, [3*60, 9 * 60, 12.5 * 60, 18 * 60, 21.5 * 60])

@dataclass
class WTemplate:
    template:   str
    packName:   str
    daySlots:   int
    dayStart:   int
    days:       tuple

    def to_1_schicht(begin, packName):
        return WTemplate(
            "1-Schicht-WU",
            packName,
            18,
            begin,
            (
                ("MO", Workday.to_1_schicht_WU(begin)),
                ("DI", Workday.to_1_schicht_WU(begin)),
                ("MI", Workday.to_1_schicht_WU(begin)),
                ("DO", Workday.to_1_schicht_WU(begin)),
                ("FR", Workday.to_1_schicht_WU(begin)),
                ("SA", Workday.to_1_schicht_WU(begin))
            ),
        )

    def to_1_schicht_holiday(begin, packName):
        return WTemplate(
            "1-Schicht-WU",
            packName,
            18,
            begin,
            (
                ("MO", Workday.to_1_schicht_WU(begin)),
                ("DI", Workday.to_1_schicht_WU(begin)),
                ("MI", Workday.to_1_schicht_WU(begin)),
                ("DO", Workday.to_holliday()),
                ("FR", Workday.to_1_schicht_WU(begin)),
                ("SA", Workday.to_1_schicht_WU(begin))
            ),
        )
        
    def to_schicht_long(begin, packName):
        return WTemplate(
            "1-Schicht",
            packName,
            19,
            begin,
            (
                ("MO", Workday.to_1_schicht(begin)),
                ("DI", Workday.to_1_schicht(begin)),
                ("MI", Workday.to_1_schicht(begin)),
                ("DO", Workday.to_1_schicht(begin)),
                ("FR", Workday.to_1_schicht(begin)),
                ("SA", Workday.to_1_schicht(begin))
            ),
        )
        
    def to_schicht_long_mischungen(begin, packName):
        return WTemplate(
            "1-Schicht+Mischungen",
            packName,
            19,
            begin,
            (
                ("MO", Workday.to_1_schicht(begin)),
                ("DI", Workday.to_1_schicht(begin)),
                ("MI", Workday.to_1_schicht(begin)),
                ("DO", Workday.to_1_schicht(begin)),
                ("FR", Workday.to_1_schicht(begin)),
                ("SA", Workday.to_1_schicht(begin))
            ),
        )

    def to_2_schicht(begin, packName):
        return WTemplate(
            "2-Schicht",
            packName,
            36,
            begin,
            (
                ("MO", Workday.to_2_schicht(begin)),
                ("DI", Workday.to_2_schicht(begin)),
                ("MI", Workday.to_2_schicht(begin)),
                ("DO", Workday.to_2_schicht(begin)),
                ("FR", Workday.to_2_schicht(begin)),
                ("SA", Workday.to_2_schicht(begin)),
            )
        )
        
    def to_2_schicht_one_only(begin, packName):
        return WTemplate(
            "2-Schicht",
            packName,
            36,
            begin,
            (
                ("MO", Workday.to_2_schicht_one_only(begin)),
                ("DI", Workday.to_2_schicht_one_only(begin)),
                ("MI", Workday.to_2_schicht_one_only(begin)),
                ("DO", Workday.to_2_schicht_one_only(begin)),
                ("FR", Workday.to_2_schicht_one_only(begin)),
                ("SA", Workday.to_2_schicht_one_only(begin)),
            )
        )
        
    def to_2_schicht_special(begin, packName):
        return WTemplate(
            "2-Schicht",
            packName,
            36,
            begin,
            (
                ("MO", Workday.to_2_schicht(begin)),
                ("DI", Workday.to_2_schicht(begin)),
                ("MI", Workday.to_2_schicht_one_only(begin)),
                ("DO", Workday.to_2_schicht_one_only(begin)),
                ("FR", Workday.to_2_schicht_one_only(begin)),
                ("SA", Workday.to_2_schicht_one_only(begin)),
            )
        )
    
    def to_3_schicht(begin, packName):
        return WTemplate(
            "3-Schicht",
            packName,
            48,
            begin,
            (
                ("MO", Workday.to_3_schicht(begin)),
                ("DI", Workday.to_3_schicht(begin)),
                ("MI", Workday.to_3_schicht(begin)),
                ("DO", Workday.to_3_schicht(begin)),
                ("FR", Workday.to_3_schicht(begin)),
                ("SA", Workday.to_3_schicht(begin)),
            )
        )


# Produktdatenbank aufbauen

In [ ]:
ibmconnect = IBMConnector(True)
prodDict = ibmconnect.getProductsTable()


# Steuerungsdaten

In [ ]:
KW = 3
YEAR = 2022

# ACHTUNG: Beim Lesen von der Dispo (FROM_DISPO = True) gehen alle bisherigen Planungen verloren!
FROM_DISPO = False   # True oder False

P1 = True
P2 = True
P3 = True
P4 = True

#DISPO = f"G:/Allgemein GmbH/Lager und Logistik/Dispo/Dispo Abpackung 2020/Dispo KW {KW-1}.xlsx"
DISPO = f"Dispo KW {KW-1}.xlsx"
PLANUNG_PATH = f"Wochenplanung KW {KW:02d}_temp.xlsx"
FINAL_PATH = f"Wochenplanung KW {KW:02d}.xlsx"
VORLAGE = "G:/Wochentakt/Packereiplanung/Vorlage/Abpackplanung Vorlage.xlsx"
# G:/Allgemein GmbH/Packerei/Abpackplanung 2021/Abpackplanung Vorlage.xlsx"
VORDEF = VORLAGE

WEEK_P1 = WTemplate.to_2_schicht(5, "Pack1")
WEEK_P2 = WTemplate.to_2_schicht(5, "Pack2")
WEEK_P3 = WTemplate.to_1_schicht(6, "Pack3")
WEEK_P4 = WTemplate.to_1_schicht(7, "Pack4")

# Leistungsdaten lesen

In [ ]:
vorlage = load_workbook(filename = VORLAGE, data_only=True)

print("Read Leistungsdaten")
sheet = vorlage["TLeistungsdaten"]
PACK_VORLAGE = packVorlage(sheet)
LEISTUNGS_DICT = packLeistung(sheet)

print("Read Produktionsstammdaten")
sheet = vorlage["ProduktionStammdaten"]
PROD_STAMM = produktionStammdaten(sheet)

vorlage.close()

# Dispo lesen & Schedule erstellen

In [ ]:
# read Schedule from Dispo
if FROM_DISPO:
    dispo = load_workbook(filename = DISPO, data_only = True, read_only = True)
    if P1: dispoP1 = readDispo(dispo["Dispo Abpackplanung P1"], LEISTUNGS_DICT)
    if P2: dispoP2 = readDispo(dispo["Dispo Abpackplanung P2"], LEISTUNGS_DICT)
    if P3: dispoP3 = readDispo(dispo["Dispo Abpackplanung P3"], LEISTUNGS_DICT)
    if P4: dispoP4 = readDispo(dispo["Dispo Abpackplanung P4"], LEISTUNGS_DICT)
    dispo.close()

    vorlage = load_workbook(filename = VORDEF, data_only = False, read_only = False)
    writeMischDispo(vorlage, dispoP1[3], dispoP2[3], dispoP3[3], dispoP4[3], prodDict)
    if P4: writeSchedule(vorlage, dispoP4, prodDict, "Pack4")
    if P3: writeSchedule(vorlage, dispoP3, prodDict, "Pack3")
    if P2: writeSchedule(vorlage, dispoP2, prodDict, "Pack2")
    if P1: writeSchedule(vorlage, dispoP1, prodDict, "Pack1")
    vorlage.save(PLANUNG_PATH)
    vorlage.close() 


In [ ]:
# Read update and write Schedule

def readSchedule(sheet):
    pas = []
    for idx, row in enumerate(sheet.rows):
        if idx == 0:
            continue

        # switch between Produktionsauftrag und Umbau / Bemerkung
        if row[0].value is None and row[1].value is None:
            # Bemerkung / Umbau
            pas.append(Bemerkung(
                pDauer= int(row[8].value),
                bemerkung= row[9].value,
                marking = row[0].fill
            ))
        else: 
            l = LEISTUNGS_DICT[row[0].value]
            pas.append(Produktionsauftrag(
                artikelNummer= row[0].value,
                artikelBezeichnung= row[1].value,
                gebindeGroesse= row[2].value,
                abpackMenge= int(row[3].value),
                anzGebinde= int(row[4].value),
                anzBeutel= int(row[5].value),
                pNumber=int(row[6].value),
                pLeistung= int(row[7].value),
                pDauer= int(row[8].value),
                bemerkung= row[9].value,
                bem_ek=row[10].value,
                roh1=row[11].value,
                roh1_bes=row[12].value,
                roh2=row[13].value,
                roh2_bes=row[14].value,
                marking = row[0].fill,
                prodDZ = l.duezi,
            ))
    return pas

def writePASchedule2(sheet, pa):
    row = sheet.max_row + 1
    
    sheet.cell(row=row, column = 9).value = pa.pDauer
    sheet.cell(row=row, column = 10).value = pa.bemerkung

    if isinstance(pa, Produktionsauftrag):
        l = getPackLeistung(pa.artikelNummer)
        if l.artikelNummer == "000000":
            print(f"Leistungsdaten für Produkt {pa.artikelNummer} nicht verfügbar!")
        
        sheet.cell(row=row, column = 1).value = pa.artikelNummer
        sheet.cell(row=row, column = 2).value = shortName(pa.artikelNummer)
        sheet.cell(row=row, column = 3).value = pa.gebindeGroesse
        sheet.cell(row=row, column = 4).value = pa.abpackMenge
        sheet.cell(row=row, column = 5).value = pa.anzGebinde
        sheet.cell(row=row, column = 6).value = pa.anzBeutel
        sheet.cell(row=row, column = 7).value = pa.pNumber
        sheet.cell(row=row, column = 8).value = pa.pLeistung
        sheet.cell(row=row, column = 11).value = pa.bem_ek
        sheet.cell(row=row, column = 12).value = pa.roh1
        sheet.cell(row=row, column = 13).value = pa.roh1_bes
        sheet.cell(row=row, column = 14).value = pa.roh2
        sheet.cell(row=row, column = 15).value = pa.roh2_bes
        if pa.marking.fgColor.rgb != "00000000":
            for i in range(1,10):
                sheet.cell(row=row, column=i).fill = pa.marking
        else:
            if l.muehleMisch:
                for i in range(2,10):
                    sheet.cell(row=row, column=i).fill = PatternFill(fgColor=purple, fill_type = 'solid')
            if l.muehle:
                for i in range(1,10):
                    sheet.cell(row=row, column=i).fill = PatternFill(fgColor=blue, fill_type = 'solid')
#            if l.duezi:
#                for i in range(1,10):
#                    sheet.cell(row=row, column=i).fill = PatternFill(fgColor=orange, fill_type = 'solid')


def writeSchedule2(vorlage, pas , pack):
    name = f"Schedule {pack}"

    sheet = vorlage.copy_worksheet(vorlage["Schedule"])
    if name in vorlage.sheetnames:
        vorlage.remove(vorlage[name])
    vorlage.move_sheet(sheet, -vorlage.index(sheet))
    sheet.title = name

    for pa in pas:
        #print(f"Trying to pack {pa.artikelNummer} with {beutelProH(pa.artikelNummer, pack)}")
        if isinstance(pa, Produktionsauftrag):
            if pa.abpackMenge is None or pa.abpackMenge == 0:
                print("This should not happen ...")
                continue

        writePASchedule2(sheet, pa)

def updateSchedule(sheet, pack):
    pas = []
    lastProd = 0

    for idx, row in enumerate(sheet.rows):
        if idx == 0:
            continue

        # switch between Produktionsauftrag und Umbau / Bemerkung
        if row[0].value is None and row[1].value is None:
            # Bemerkung / Umbau
            pas.append(Bemerkung(
                pDauer= int(row[8].value),
                bemerkung= row[9].value,
                marking = copy(row[0].fill)
            ))
        else:
            prod = prodDict.get(f"s{row[0].value}", None)
            if prod is None:
                print(f"Could not find product data of {row[0].value}")
            bundle = Bundle.fromString(prod.bundle)
            amount = int(row[3].value)
            nbrBags = int(amount * 1000 / bundle.bagWeight) if row[5].value is None else int(row[5].value)
            nbrBundles = int(nbrBags / bundle.nbrBags) if row[4].value is None else int(row[4].value)
            performance = int(row[7].value)
            if performance is None:
                l = getPackLeistung(prod.number[1:])
                if l.artikelNummer == "000000":
                    print(f"Leistungsdaten für Produkt {prod.number} nicht verfügbar!")
                
                performance = l.leistung.get(pack)
                if performance is None:
                    print(f"Leistungsdaten für Produkt {prod.number} auf Packerei {pack} nicht verfügbar!")

            prodNr = lastProd + 1
            if not row[6].value is None:
                prodNr = int(row[6].value)
            lastProdNr = prodNr
        

            pas.append(Produktionsauftrag(
                artikelNummer= prod.number[1:],
                artikelBezeichnung= prod.name,
                gebindeGroesse= bundle.szBundle,
                abpackMenge= amount,
                anzGebinde= nbrBundles,
                anzBeutel= nbrBags,
                pNumber = prodNr,
                pLeistung= performance,
                pDauer= prodTime(nbrBags, performance) if row[8].value is None else row[8].value,
                bemerkung= row[9].value,
                bem_ek = row[10].value,
                roh1=row[11].value,
                roh1_bes=row[12].value,
                roh2=row[13].value,
                roh2_bes=row[14].value,
                marking = copy(row[0].fill),
                prodDZ = prod.pickArea == "33"
            ))
    return pas

# Produktionsplanung schreiben

nimmt die Schedule und schreibt sie in die Abpackplanungsdatei

In [ ]:
# classes Produktionsauftrag & Bemerkung
@dataclass
class Produktionsauftrag:
    artikelNummer:      str
    artikelBezeichnung: str
    gebindeGroesse:     str
    abpackMenge:        int
    anzGebinde:         int
    anzBeutel:          int
    pNumber:            int
    pLeistung:          int
    pDauer:             int
    bemerkung:          str
    bem_ek:             str
    roh1:               str     # Rohstoff 1
    roh1_bes:           str     # Rohstoff 1 Bestand
    roh2:               str     # Rohstoff 2
    roh2_bes:           str     # Rohstoff 2 Bestand
    marking:            PatternFill
    prodDZ:             bool

@dataclass
class Bemerkung:
    pDauer:             int
    bemerkung:          str
    marking:            PatternFill

    def isSimpleProdChange(self):
        return self.bemerkung is None or self.bemerkung == ""


In [ ]:
# write Schedule to factory plan

def toTimeString(minutes):
    return f"{int(minutes / 60):2}:{int(minutes % 60):02}"

def toTimeSlotString(minutes):
    return f"{toTimeString(minutes)} - {toTimeString(minutes + 30)}"


def fillWorkday(sheet, kw, year, wtemplate):
    pack = wtemplate.packName
    workday = wtemplate.days[0][1]
    # header
    sheet.cell(row=1, column=1).value = f"Produktionsplanung {pack}"
    now = datetime.datetime.now().strftime("%d.%m.%Y: %H:%M")
    sheet.cell(row=wtemplate.daySlots + 14, column=1).value = f"Stand {now}"
    sheet.cell(row=2, column=2).value = kw
    sheet.cell(row=3, column=2).value = year
    sheet.cell(row=3, column=1).value = pack

    current = workday.begin * 60
    row = 4
    while current < workday.end * 60:
        sheet.cell(row=row, column=2).value = toTimeSlotString(current)
        current += 30
        if current >= 24*60:
            current = 0
        row += 1

def writeToPlan(sheet, pa, day, startSlot, timeEnd, prodDict, workday):
    if isinstance(pa, Produktionsauftrag):
        writePA(sheet, pa, day, startSlot, prodDict, workday)
    else:
        writeComment(sheet, pa, day, startSlot, timeEnd, prodDict, workday)
        

def writeComment(sheet, pa, day, startSlot, timeEnd, prodDict, workday):
    assert isinstance(pa, Bemerkung), "Trying to write PA as Break"

    if pa.pDauer < 30 or pa.bemerkung is None:
        return

    columns = { "MO": 3, "DI": 13, "MI":23, "DO":33, "FR":43, "SA":53 }
    columnOffset=columns[day]
    rowOffset = 4

    lastSlot = slot(timeEnd)

    sheet.cell(row=rowOffset + startSlot, column=columnOffset+4).value=pa.bemerkung
    current = startSlot
    while True:
        if not slotIsBreak(current, workday):
            sheet.cell(row=rowOffset+current, column=columnOffset+4).fill = PatternFill(fgColor=red, fill_type = 'solid')
        current += 1
        if current >= lastSlot:
            break

def writePA(sheet, pa, day, startSlot, prodDict, workday):
    assert isinstance(pa, Produktionsauftrag), "Trying to write Break as PA"
    
    columns = { "MO": 3, "DI": 13, "MI":23, "DO":33, "FR":43, "SA":53 }
    columnOffset=columns[day]
    rowOffset = 4
    
    sheet.cell(row=rowOffset+startSlot, column=columnOffset+0).value = pa.anzBeutel
    sheet.cell(row=rowOffset+startSlot, column=columnOffset+1).value = pa.anzGebinde
    if pa.artikelNummer is None:
        sheet.cell(row=rowOffset+startSlot, column=columnOffset+2).value = pa.gebindeGroesse
        sheet.cell(row=rowOffset+startSlot, column=columnOffset+4).value = pa.artikelBezeichnung
    else:
        sheet.cell(row=rowOffset+startSlot, column=columnOffset+3).value = f"p{pa.artikelNummer}"
    sheet.cell(row=rowOffset+startSlot, column=columnOffset+7).value = pa.abpackMenge
    prod = prodDict.get(pa.artikelNummer, None)
    sheet.cell(row=rowOffset+startSlot, column=columnOffset+6).value = math.ceil(pa.anzGebinde / prod.palSize) if not prod is None else None
    if pa.bemerkung != "" and not pa.bemerkung is None and pa.pDauer >= 60:
        sheet.cell(row=rowOffset + startSlot + 1, column=columnOffset+4).value=pa.bemerkung
        sheet.cell(row=rowOffset + startSlot + 1, column=columnOffset+4).fill = PatternFill(fgColor=yellow, fill_type = 'solid')
    if not pa.marking is None:
        for i in range(8):
            sheet.cell(row=rowOffset+startSlot, column=columnOffset+i).fill = pa.marking
    if pa.prodDZ:
            sheet.cell(row=rowOffset+startSlot, column=columnOffset+0).fill = PatternFill(fgColor=orange, fill_type = 'solid')
            sheet.cell(row=rowOffset+startSlot, column=columnOffset+1).fill = PatternFill(fgColor=orange, fill_type = 'solid')
            sheet.cell(row=rowOffset+startSlot, column=columnOffset+2).fill = PatternFill(fgColor=orange, fill_type = 'solid')

def writeZeitVerschn(sheet, slotsPerDay, day, uebertragZ):
    columns = { "MO": 3, "DI": 13, "MI":23, "DO":33, "FR":43, "SA":53 }
    columnOffset=columns[day]
    rowOffset = 4
    sheet.cell(row=rowOffset+slotsPerDay, column=columnOffset+2).value = uebertragZ

            
def writeNegUebertrag(sheet, slotsPerDay, day, uebertrag):
    columns = { "MO": 3, "DI": 13, "MI":23, "DO":33, "FR":43, "SA":53 }
    columnOffset=columns[day]
    rowOffset = 4
    sheet.cell(row=rowOffset+slotsPerDay-1, column=columnOffset+0).value = -uebertrag
    
def writePosUebertrag(sheet, slotsPerDay, day, uebertrag):
    columns = { "MO": 3, "DI": 13, "MI":23, "DO":33, "FR":43, "SA":53 }
    columnOffset=columns[day]
    rowOffset = 4
    sheet.cell(row=rowOffset, column=columnOffset+0).value = uebertrag
    sheet.cell(row=rowOffset, column=columnOffset+1).value = "Rest"
    sheet.cell(row=rowOffset, column=columnOffset+6).value = ""

In [ ]:
# write Schedule to factory plan 2
def slot(time):
    return max(0, math.floor(time / 30))

def slotIsBreak(s, workday):
    breakSlots = set(map(lambda b: slot(b), workday.breaks))

    return s in breakSlots

def timeAdd(current, add,  breaks):
    newTime = current + add
    # find the next break
    nextBreak = 0
    while nextBreak < len(breaks):
        if breaks[nextBreak] > current:
            break
        nextBreak += 1

    # next break settled
    for b in breaks[nextBreak:-1]:
        if b <= newTime:
            newTime += 30

    return (newTime, breaks[-1] - newTime)


def writeAbpackplan(vorlage, wtemplate, schedule, prodDict, p2=False):
    days = wtemplate.days
    sheet = vorlage.copy_worksheet(vorlage[wtemplate.template])
    if wtemplate.packName in vorlage.sheetnames:
        vorlage.remove(vorlage[wtemplate.packName])
    vorlage.move_sheet(sheet, -vorlage.index(sheet))
    sheet.title = wtemplate.packName


    time = 15
    paIdx = 0
    remainingT = 0
    uebertrag = None
    fillWorkday(sheet, KW, YEAR, wtemplate)
    
    for day, schicht in wtemplate.days:
        if schicht.begin == schicht.end:
            # holliday
            continue
        
        dayLength = (schicht.end - schicht.begin) * 60
        breaks = schicht.breaks + [(schicht.end - schicht.begin) * 60,]
        slotsPerDay = wtemplate.daySlots
        time, remainingT = timeAdd(schicht.begin - wtemplate.dayStart, remainingT, breaks)
        currentSlot = slot(time)
        if not uebertrag is None:
            writePosUebertrag(sheet, slotsPerDay, day, uebertrag)
            uebertrag = None
            
            if remainingT < 0:    # running into the next day
                uebertragVerhältnis = -remainingT / currentPA.pDauer
                uebertragMenge = int(uebertragVerhältnis * currentPA.anzBeutel)

                writeNegUebertrag(sheet, slotsPerDay + 1, day, uebertragMenge)
                uebertrag = uebertragMenge

                remainingT = -remainingT
                continue

            remainingT = 15 + max(15, remainingT )
            

        while paIdx < len(schedule):
            currentPA = schedule[paIdx]        
            if remainingT <= 15 and currentPA.pDauer > 30:
                time = 15
                break

            currentSlot = slot(time)
            newtime, remainingT = timeAdd(time, currentPA.pDauer, breaks)

            writeToPlan(sheet, currentPA, day, currentSlot, newtime, prodDict, schicht)
            lastSlot = currentSlot
            
            if remainingT < 0:    # running into the next day
                if remainingT < -15:
                    if type(currentPA) == Produktionsauftrag:
                        uebertragVerhältnis = -remainingT / currentPA.pDauer
                        uebertragMenge = int(uebertragVerhältnis * currentPA.anzBeutel)

                        writeNegUebertrag(sheet, slotsPerDay + 1, day, uebertragMenge)
                        uebertrag = uebertragMenge
                    remainingT = -remainingT
                else:
                    uebertrag = None
                    remainingT = 0

                paIdx += 1
                break

            paIdx += 1
            time = newtime

    if paIdx < len(schedule):
            print(f"Week is full!")


# Update Schedule

In [ ]:
vorlage = load_workbook(filename = PLANUNG_PATH, data_only = False, read_only = False)
try:
    if P4:
        print("Updating P4 ...")
        scheduleP4 = updateSchedule(vorlage["Schedule Pack4"], "Pack4")
        writeSchedule2(vorlage, scheduleP4, "Pack4")
        writeAbpackplan(vorlage, WEEK_P4, scheduleP4, prodDict)
    if P3:
        print("Updating P3 ...")
        scheduleP3 = updateSchedule(vorlage["Schedule Pack3"], "Pack3")
        writeSchedule2(vorlage, scheduleP3, "Pack3")
        writeAbpackplan(vorlage, WEEK_P3, scheduleP3, prodDict)
    if P2: 
        print("Updating P2 ...")
        scheduleP2 = updateSchedule(vorlage["Schedule Pack2"], "Pack1")
        writeSchedule2(vorlage, scheduleP2, "Pack2")
        writeAbpackplan(vorlage, WEEK_P2, scheduleP2, prodDict)
    if P1:
        print("Updating P1 ...")
        scheduleP1 = updateSchedule(vorlage["Schedule Pack1"], "Pack1")
        writeSchedule2(vorlage, scheduleP1, "Pack1")
        writeAbpackplan(vorlage, WEEK_P1, scheduleP1, prodDict)

    sheet = vorlage["Mischungen"]
    sheet["B2"] = KW
    
    print("\nWriting to file ...")
    vorlage.save(PLANUNG_PATH)
    print("done!")
except PermissionError:
    print(f"Saving the Excel file failed. Is it still open?")
finally:
    vorlage.close()

# Produktionsplanung finalisieren

In [ ]:
def finalizeSheet(sheet):
    for row in sheet.iter_rows():
        for cell in row:
            if cell.value == "#N/A":
                cell.value = None 

def finalize(vorlage):
    for pack in ["Mischungen", "Pack4", "Pack3", "Pack2", "Pack1"]:
    #for pack in ["Pack3", "Pack2", "Pack1"]:
        sheet = vorlage[pack]
        vorlage.move_sheet(sheet, -vorlage.index(sheet))
        finalizeSheet(vorlage[pack])
    
    sheet = vorlage["Mischungen"]
    sheet["B2"] = KW
    vorlage.move_sheet(sheet, -vorlage.index(sheet) + 4)
    
    removeUnused(vorlage)
    
def removeUnused(vorlage):
    vorlage.remove(vorlage["Schedule"])
    vorlage.remove(vorlage["1-Schicht"])
    vorlage.remove(vorlage["1-Schicht-WU"])
    vorlage.remove(vorlage["1-Schicht+Mischungen"])
    vorlage.remove(vorlage["2-Schicht"])
    vorlage.remove(vorlage["3-Schicht"])
    vorlage.remove(vorlage["ProduktionStammdaten"])
    vorlage.remove(vorlage["TLeistungsdaten"])
    vorlage.remove(vorlage["Artikelstamm"])

try:
    weekPlan = load_workbook(filename = PLANUNG_PATH, data_only = True, read_only = False)
    
    finalize(weekPlan)
    weekPlan.save(FINAL_PATH)
except :
    print(f"Saving the Excel file {FINAL_PATH} failed. Is it still opened?")
finally:
    weekPlan.close()

# Create List of WG Brackenheim products

In [ ]:
from openpyxl.styles import Border, Side
thin = Side(border_style="thin", color="000000")

productset = [p for p in scheduleP1 if isinstance(p, Produktionsauftrag)]
productset.extend([p for p in scheduleP2 if isinstance(p, Produktionsauftrag)])
productset.extend([p for p in scheduleP4 if isinstance(p, Produktionsauftrag)])

FINAL = f"WG Brackenheim KW{KW}.xlsx"
VORLAGE = f"Dürrenzimmernvorlage.xlsx"
vorlage = load_workbook(VORLAGE, data_only=False, read_only = False)
sheet = vorlage.active
try:
    row = 3
    for pa in productset:
        prod = prodDict[pa.artikelNummer]
        if prod.pickArea != "33":
            continue
        sheet.cell(row = row, column = 1).value = pa.artikelNummer
        sheet.cell(row = row, column = 1).border = Border(bottom=thin, top=thin)
        sheet.cell(row = row, column = 2).value = pa.artikelBezeichnung
        sheet.cell(row = row, column = 2).border = Border(bottom=thin, top=thin)
        sheet.cell(row = row, column = 3).value = prod.bundle
        sheet.cell(row = row, column = 3).border = Border(bottom=thin, top=thin)
        sheet.cell(row = row, column = 4).value = math.ceil(pa.anzGebinde / (prod.palSize * 2 if prod.palSize == 64 else prod.palSize))
        sheet.cell(row = row, column = 4).border = Border(bottom=thin, top=thin)
        row += 1
    vorlage.save(FINAL)
finally:
    vorlage.close()

# Create a checklist for bags

In [ ]:
PLANUNG_PATH_OLD = f"Wochenplanung KW {KW-1:02d}_temp.xlsx"
scheduleOld = load_workbook(filename = PLANUNG_PATH_OLD, data_only = False, read_only = False)
try:
    scheduleP4Old = readSchedule(scheduleOld["Schedule Pack4"])
    scheduleP2Old = readSchedule(scheduleOld["Schedule Pack2"])
    scheduleP1Old = readSchedule(scheduleOld["Schedule Pack1"])
except PermissionError:
    print(f"Reading the Excel file {PLANUNG_PATH_OLD} failed. Is it still open?")
finally:
    scheduleOld.close()


In [ ]:
productset = [p.artikelNummer for p in scheduleP1Old if isinstance(p, Produktionsauftrag)]
productset.extend([p.artikelNummer for p in scheduleP2Old if isinstance(p, Produktionsauftrag)])
productset.extend([p.artikelNummer for p in scheduleP4Old if isinstance(p, Produktionsauftrag)])

HLB_COUNT_PATH = f"Zaehlliste KW{KW-1}.xlsx"
HLB_VORLAGE_PATH = "Abruf HLB Vorlage - Lagerplätze.xlsx"
vorlage_hlb = load_workbook(HLB_VORLAGE_PATH, data_only=True, read_only = False)
sheet = vorlage_hlb["Tüten HLB"]
header = ["Artikelnr. Tüten", "Format", "Artikelnr. VP", "Bezeichnung", "Tütengröße", "Menge pro Karton", "", "Marke", "Lagerplatz Reihe", "Lagerplatz Position", "Bemerkungen", "Kartons", "Stück", "Bestellung Karton", "In Stück"]
to_count = set()
try:
    for row in sheet.iter_rows(min_row=2, max_row=len(sheet['A']), max_col=15, values_only=True):
        artNr = row[2]
        if artNr in productset:
            to_count.add(row)
finally:
    vorlage_hlb.close()

In [ ]:
hlb_count = Workbook()
sheet = hlb_count.active
sheet.title = "HLB Tüten"
try:
    sheet.append((header))
    to_count_list = list()
    to_count_list.extend(to_count)
    to_count_list.sort(key = lambda i: i[2])
    for row in to_count_list:
        sheet.append(row)
    
    tab = Table(displayName="Counting", ref=f"A1:O{len(to_count_list)+2}")

    sheet.add_table(tab)
    hlb_count.save(HLB_COUNT_PATH)
finally:
    hlb_count.close()